# Machine Learning Examples using datasets on QCArchive

The notebook provides two ML examples:

- Unsupervised learning: use manifold learning to understand the structure of the QM7b, QM7b-T, and SN2 Reaction datasets. 
- Supervised learning: train a kernel model to predict atomization energies with the ANI-1 dataset, and test it on a COMP6 benchmark.

Begin by connecting to the MolSSI server:

In [3]:
import numpy as np
import pandas as pd

import qcportal as ptl

client = ptl.FractalClient()

## Unsupervised learning: manifold learning with QM7b, QM7b-T, and SN2 Reactions

<img src="https://umap-learn.readthedocs.io/en/latest/_static/logo.png" alt="UMAP" align="left" style="width: 120px;"/>
Manifold learning is a strategy for exposing the structure of high-dimensional datasets through non-linear dimensionality reduction. In this example, we will look at the similarities and differences within and between three ML datasets. Molecules will be fingerprinted by Coulomb matrix features, and manifold learning will be performed with the Uniform Manifold Approximation and Projection (UMAP) method. 

https://umap-learn.readthedocs.io/en/latest/



In [4]:
qm7b = client.get_collection("dataset", "qm7b")
print_info(qm7b)

Name: QM7b

Data Points: 7211
Elements: ['C', 'H', 'Cl', 'N', 'O', 'S']
Labels: ['atomization energy', 'excitation energy', 'lumo', 'ionization potential', 'electron affinity', 'polarizability', 'absorption intensity', 'homo']


### Generating coulomb matrix features

`Molecule` objects contain information about atomic symbols/numbers, geometry, charge, spin, fragments, etc. As an example of using this information, the `coulomb_matrix` function below computes the (sorted) Coulomb matrix features corresponding to a `Molecule`. The Coulomb matrix is given by:

<img src=https://pubs.rsc.org/image/article/2018/sc/c7sc02664a/c7sc02664a-t3_hi-res.gif width=250>

Coulomb matrix features are not the most sophisticated, but they are simple to implement:

In [5]:
import qcelemental
scale = qcelemental.constants.conversion_factor("bohr", "angstrom") * np.sqrt(2)

def coulomb_matrix(mol, size=23):
    """
    Compute the sorted Coulomb matrix features corresponding to a molecules
    
    Parameters
    ----------
    mol: Molecule
        the molecule whose features are to be computed
    size: int, optional
        maximum dimension of the Coulomb matrix
    """
    natoms = len(mol.atomic_numbers)
    
    # Create the Coulomb matrix
    M = np.zeros((natoms, natoms))
    for i in range(natoms):
        M[i,i] = 0.5 * mol.atomic_numbers[i]**2.4
        for j in range(0,i):
            M[i,j] = mol.atomic_numbers[i] * mol.atomic_numbers[j] / \
                np.linalg.norm(mol.geometry[i,:] - mol.geometry[j,:] * scale )
            M[j,i] = M[i,j]
            
    # Sort based on row norm, and zero-pad or truncate to size
    order = np.argsort(np.linalg.norm(M, axis=0))[::-1][:size]
    ret = np.zeros((size, size))
    for i in range(min(natoms, size)):
        for j in range(min(natoms, size)):
            ret[i,j] = M[order[i], order[j]]
    
    # Flatten upper triangle to 1D
    return ret[np.triu_indices(size)]

Compute the Coulomb matrix feature for each molecule. The code below creates a new column in the `DataFrame` containing the features.

In [6]:
qm7b_mols = qm7b.get_molecules()
qm7b_mols["feature"] = [coulomb_matrix(molecule) for molecule in qm7b_mols["molecule"]]
qm7b_mols

molecule  \
index                                                      
0          Geometry (in Angstrom), charge = 0.0, mult...   
1          Geometry (in Angstrom), charge = 0.0, mult...   
10         Geometry (in Angstrom), charge = 0.0, mult...   
100        Geometry (in Angstrom), charge = 0.0, mult...   
1000       Geometry (in Angstrom), charge = 0.0, mult...   
...                                                  ...   
995        Geometry (in Angstrom), charge = 0.0, mult...   
996        Geometry (in Angstrom), charge = 0.0, mult...   
997        Geometry (in Angstrom), charge = 0.0, mult...   
998        Geometry (in Angstrom), charge = 0.0, mult...   
999        Geometry (in Angstrom), charge = 0.0, mult...   

                                                 feature  
index                                                     
0      [36.85810519942594, 3.0602011490558505, 3.0553...  
1      [36.85810519942594, 10.707116135022035, 3.0751...  
10     [53.3587073998281, 12.483520879461704, 7.74603...  
100    [53.3587073998281, 7.416502178204354, 10.61293...  
1000   [73.51669471981023, 10.524193502952423, 4.7371...  
...                                                  ...  
995    [73.51669471981023, 12.945983223622989, 6.2342...  
996    [73.51669471981023, 17.492583403086307, 17.890...  
997    [73.51669471981023, 13.44823763751797, 8.96043...  
998    [73.51669471981023, 13.374609104346993, 8.7642...  
999    [73.51669471981023, 12.325415318305255, 13.542...  

[7211 rows x 2 columns]

### Manifold learning with UMAP

Often in ML, features live in a high-dimensional space, but may have low dimensional structure. To examine this, we use UMAP to reduce the Coulomb matrix features of QM7b onto two dimensions:

In [7]:
import umap
import warnings; warnings.simplefilter('ignore')  # supress numba warnings

reducer = umap.UMAP()
X = np.vstack(qm7b_mols["feature"])  # format features into matrix for UMAP
embedding = reducer.fit_transform(X)
print(f"Feature matrix shape: {X.shape}")
print(f"UMAP embedding shape: {embedding.shape}")

Feature matrix shape: (7211, 276)
UMAP embedding shape: (7211, 2)


In [8]:
import plotly.express as px

qm7b_mols["Embedding Dim. 1"] = embedding[:, 0]
qm7b_mols["Embedding Dim. 2"] = embedding[:, 1]

fig = px.scatter(qm7b_mols, x="Embedding Dim. 1", y="Embedding Dim. 2", title="UMAP Embedding of QM7b")
fig.show()

Coloring by unique heavy atoms shows that Coulomb matrix features cluster according to chemical element. This leads to a lack of "alchemical transferability", a know deficiency of these features.

In [9]:
qm7b_mols["Heavy Atoms"] = [frozenset(set(mol.symbols)-set(['H'])) for mol in qm7b_mols["molecule"]]

fig = px.scatter(qm7b_mols, x="Embedding Dim. 1", y="Embedding Dim. 2", color="Heavy Atoms", 
                 title="UMAP Embedding of QM7b, Colored by Elements")
fig.show()

### Combining multiple datasets

Because all data in the QCArchive follow the same format, we can easily combine data from multiple datasets. Below, we use UMAP to compare two additional datasets to QM7b.


QM7b-T is chemically similar to QM7b, containing thermalized geometries corresponding to the optimized geometries in QM7b:

In [10]:
qm7bT = client.get_collection("Dataset", "QM7b-T")
print_info(qm7bT)

Name: QM7b-T

Data Points: 7211
Elements: ['C', 'H', 'Cl', 'N', 'O', 'S']
Labels: ['energy']


----

The SN2 Reactions dataset is different to QM7b, containing different chemical elements as well as ions:

In [11]:
sn2 = client.get_collection("Dataset", "SN2 Reactions")
print_info(sn2)

Name: SN2 Reactions

Data Points: 452709
Elements: ['C', 'H', 'Br', 'Cl', 'F', 'I']
Labels: ['energy', 'gradient', 'dipole']


----

As before, molecules are obtained from the datasets with `get_molecules`, and Coulomb matrix features corresponding to those molecules are generated. For the case of SN2, 2,000 molecules are sampled from a total of 452,709.

In [12]:
qm7bT_mols = qm7bT.get_molecules()
qm7bT_mols["feature"] = [coulomb_matrix(molecule) for molecule in qm7bT_mols["molecule"]]

index = sn2.get_entries().sample(n=2000, axis=0)
sn2_mols = sn2.get_molecules(subset=list(index["name"]))
sn2_mols["feature"] = [coulomb_matrix(molecule) for molecule in sn2_mols["molecule"]]

An example molecule from the SN2 Reactions dataset:

In [13]:
sn2_mols["molecule"][15]

_ColormakerRegistry()

NGLWidget()

Comibine all of the data into one `DataFrame`:

In [14]:
qm7b_mols["Dataset"] = "QM7b"
qm7bT_mols["Dataset"] = "QM7b-T"
sn2_mols["Dataset"] = "SN2"
all_mols = qm7b_mols.append(qm7bT_mols, sort=False).append(sn2_mols, sort=False)

And repeat the UMAP process:

In [15]:
reducer = umap.UMAP()
X = np.vstack(all_mols["feature"])
embedding = reducer.fit_transform(X)

all_mols["Embedding Dim. 1"] = embedding[:, 0]
all_mols["Embedding Dim. 2"] = embedding[:, 1]

fig = px.scatter(all_mols, x="Embedding Dim. 1", y="Embedding Dim. 2", color="Dataset",
                title="UMAP Embedding of QM7b, QM7b-T, and SN2, Colored by Dataset")
fig.show()

We see that the QM7b and QM7b-T datasets overlap in the space of Coulomb features, no suprise given their similarity. The SN2 Reaction dataset, comprised of different chemical elements, has no overlap with the other two datasets.

# Supervised learning: training a kernel model to predict DFT energies

ANI-1 is a dataset of over 22 million calculations:

In [16]:
ani1 = client.get_collection("Dataset", "ANI-1")
print_info(ani1)

Name: ANI-1

Data Points: 22057374
Elements: ['C', 'H', 'N', 'O']
Labels: ['energy']


### Creating a test and training set

Because it is so large (10 GB), we only want to pull down a subset of ANI-1's data. We start by getting the `index`, the list of the names of the 22 million entries in ANI-1.

In [ ]:
ani_index = ani1.get_index()

The first 10 names are:

In [17]:
ani_index[:10]

['gdb11_s01-0-0',
 'gdb11_s01-0-1',
 'gdb11_s01-0-2',
 'gdb11_s01-0-3',
 'gdb11_s01-0-4',
 'gdb11_s01-0-5',
 'gdb11_s01-0-6',
 'gdb11_s01-0-7',
 'gdb11_s01-0-8',
 'gdb11_s01-0-9']

We will construct a training set of 1,000 molecules and a test set of 100 molecules.

In [18]:
import sklearn.model_selection

index_train, index_test = sklearn.model_selection.train_test_split(ani_index, 
                                                                   train_size=1000, 
                                                                   test_size=100)

### Obtaining molecules and features

By default, `get_molecules` returns all molecules in a dataset. The `subset` option allows us to only return a subset of the total data.

In [19]:
mols_train = ani1.get_molecules(subset=index_train)
mols_test  = ani1.get_molecules(subset=index_test)

mols_train

molecule
index                                                                 
gdb11_s08-1065-136       Geometry (in Angstrom), charge = 0.0, mult...
gdb11_s04-23-9088        Geometry (in Angstrom), charge = 0.0, mult...
gdb11_s08-37758-164      Geometry (in Angstrom), charge = 0.0, mult...
gdb11_s07-1736-599       Geometry (in Angstrom), charge = 0.0, mult...
gdb11_s07-2195-15        Geometry (in Angstrom), charge = 0.0, mult...
...                                                                ...
gdb11_s08-21374-45       Geometry (in Angstrom), charge = 0.0, mult...
gdb11_s05-193-1649       Geometry (in Angstrom), charge = 0.0, mult...
gdb11_s05-57-5967        Geometry (in Angstrom), charge = 0.0, mult...
gdb11_s07-3769-379       Geometry (in Angstrom), charge = 0.0, mult...
gdb11_s08-27091-83       Geometry (in Angstrom), charge = 0.0, mult...

[1000 rows x 1 columns]

In [33]:
mols_train["molecule"][321]

NGLWidget()

Construct Coulomb matrix features in the same manner as in the previous example:

In [21]:
mols_train["feature"] = [coulomb_matrix(molecule) for molecule in mols_train["molecule"]]
mols_test["feature"]  = [coulomb_matrix(molecule) for molecule in mols_test["molecule"]]

mols_train

molecule  \
index                                                                    
gdb11_s08-1065-136       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s04-23-9088        Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s08-37758-164      Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s07-1736-599       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s07-2195-15        Geometry (in Angstrom), charge = 0.0, mult...   
...                                                                ...   
gdb11_s08-21374-45       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s05-193-1649       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s05-57-5967        Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s07-3769-379       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s08-27091-83       Geometry (in Angstrom), charge = 0.0, mult...   

                                                               feature  
index                                                                   
gdb11_s08-1065-136   [53.3587073998281, 8.908692425554532, 8.874621...  
gdb11_s04-23-9088    [73.51669471981023, 22.67212602609652, 12.0400...  
gdb11_s08-37758-164  [53.3587073998281, 8.082911344753562, 8.080247...  
gdb11_s07-1736-599   [73.51669471981023, 13.567652117139643, 8.6530...  
gdb11_s07-2195-15    [73.51669471981023, 16.296006930193187, 12.602...  
...                                                                ...  
gdb11_s08-21374-45   [53.3587073998281, 19.052463779247958, 5.95931...  
gdb11_s05-193-1649   [73.51669471981023, 15.580992353082049, 9.3382...  
gdb11_s05-57-5967    [73.51669471981023, 22.423817905692996, 24.156...  
gdb11_s07-3769-379   [73.51669471981023, 11.152141192626104, 11.212...  
gdb11_s08-27091-83   [53.3587073998281, 23.5715179759266, 30.188533...  

[1000 rows x 2 columns]

### Obtaining properties and labels

For supervised learning, we need labels in addition to features. The `list_values` function describes what properties are available. For the case of the ANI-1 dataset, the only property is the ωB97x/6-31(d) energy.

In [22]:
ani1.list_values()

keywords                  name
native driver program  method basis                                 
False  energy Gaussian ωB97x  6-31(d)  Unknown  ωB97x/6-31(d) Energy

The `get_values` function pulls a data column down from the server. Values may be filtered by any of the fields described in `list_values`, including `driver`, `program`, `method`, `basis`, and `name`. Just like in `get_molecules`, the `subset` option allows us to only return a subset of the total data.

In [23]:
ani1.units = "hartree"
values_train = ani1.get_values(name="ωB97x/6-31(d) Energy", subset=index_train)
values_test  = ani1.get_values(name="ωB97x/6-31(d) Energy", subset=index_test)

values_train

ωB97x/6-31(d) Energy
gdb11_s08-1065-136              -330.276
gdb11_s04-23-9088               -193.028
gdb11_s08-37758-164             -326.598
gdb11_s07-1736-599              -377.689
gdb11_s07-2195-15               -341.565
...                                  ...
gdb11_s08-21374-45              -361.028
gdb11_s05-193-1649              -264.398
gdb11_s05-57-5967               -232.342
gdb11_s07-3769-379              -326.965
gdb11_s08-27091-83                -391.9

[1000 rows x 1 columns]

Combine the molecules, feautres and energies into a single `DataFrame`:

In [24]:
data_train = pd.merge(values_train, mols_train, left_index=True, right_index=True)
data_test  = pd.merge(values_test,  mols_test,  left_index=True, right_index=True)

data_train

ωB97x/6-31(d) Energy  \
gdb11_s08-1065-136              -330.276   
gdb11_s04-23-9088               -193.028   
gdb11_s08-37758-164             -326.598   
gdb11_s07-1736-599              -377.689   
gdb11_s07-2195-15               -341.565   
...                                  ...   
gdb11_s08-21374-45              -361.028   
gdb11_s05-193-1649              -264.398   
gdb11_s05-57-5967               -232.342   
gdb11_s07-3769-379              -326.965   
gdb11_s08-27091-83                -391.9   

                                                              molecule  \
gdb11_s08-1065-136       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s04-23-9088        Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s08-37758-164      Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s07-1736-599       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s07-2195-15        Geometry (in Angstrom), charge = 0.0, mult...   
...                                                                ...   
gdb11_s08-21374-45       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s05-193-1649       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s05-57-5967        Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s07-3769-379       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s08-27091-83       Geometry (in Angstrom), charge = 0.0, mult...   

                                                               feature  
gdb11_s08-1065-136   [53.3587073998281, 8.908692425554532, 8.874621...  
gdb11_s04-23-9088    [73.51669471981023, 22.67212602609652, 12.0400...  
gdb11_s08-37758-164  [53.3587073998281, 8.082911344753562, 8.080247...  
gdb11_s07-1736-599   [73.51669471981023, 13.567652117139643, 8.6530...  
gdb11_s07-2195-15    [73.51669471981023, 16.296006930193187, 12.602...  
...                                                                ...  
gdb11_s08-21374-45   [53.3587073998281, 19.052463779247958, 5.95931...  
gdb11_s05-193-1649   [73.51669471981023, 15.580992353082049, 9.3382...  
gdb11_s05-57-5967    [73.51669471981023, 22.423817905692996, 24.156...  
gdb11_s07-3769-379   [73.51669471981023, 11.152141192626104, 11.212...  
gdb11_s08-27091-83   [53.3587073998281, 23.5715179759266, 30.188533...  

[1000 rows x 3 columns]

For this example, our labels will be atomization energies:

In [25]:
def free_atom_energy(molecule):
    """ Returns the energy of the atoms in the molecule separated to infinity."""
    
    free_atom_ref = {"H": -0.500607632585, "C": -37.8302333826, "N": -54.5680045287, "O": -75.0362229210}
    return sum((free_atom_ref[atom] for atom in molecule.symbols))

data_train["label"] = [data_train.loc[idx, "ωB97x/6-31(d) Energy"] - 
                       free_atom_energy(data_train.loc[idx, "molecule"])
                       for idx in data_train.index]
data_test["label"]  = [data_test.loc[idx, "ωB97x/6-31(d) Energy"] - 
                       free_atom_energy(data_test.loc[idx, "molecule"])
                       for idx in data_test.index]

data_train

ωB97x/6-31(d) Energy  \
gdb11_s08-1065-136              -330.276   
gdb11_s04-23-9088               -193.028   
gdb11_s08-37758-164             -326.598   
gdb11_s07-1736-599              -377.689   
gdb11_s07-2195-15               -341.565   
...                                  ...   
gdb11_s08-21374-45              -361.028   
gdb11_s05-193-1649              -264.398   
gdb11_s05-57-5967               -232.342   
gdb11_s07-3769-379              -326.965   
gdb11_s08-27091-83                -391.9   

                                                              molecule  \
gdb11_s08-1065-136       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s04-23-9088        Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s08-37758-164      Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s07-1736-599       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s07-2195-15        Geometry (in Angstrom), charge = 0.0, mult...   
...                                                                ...   
gdb11_s08-21374-45       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s05-193-1649       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s05-57-5967        Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s07-3769-379       Geometry (in Angstrom), charge = 0.0, mult...   
gdb11_s08-27091-83       Geometry (in Angstrom), charge = 0.0, mult...   

                                                               feature  \
gdb11_s08-1065-136   [53.3587073998281, 8.908692425554532, 8.874621...   
gdb11_s04-23-9088    [73.51669471981023, 22.67212602609652, 12.0400...   
gdb11_s08-37758-164  [53.3587073998281, 8.082911344753562, 8.080247...   
gdb11_s07-1736-599   [73.51669471981023, 13.567652117139643, 8.6530...   
gdb11_s07-2195-15    [73.51669471981023, 16.296006930193187, 12.602...   
...                                                                ...   
gdb11_s08-21374-45   [53.3587073998281, 19.052463779247958, 5.95931...   
gdb11_s05-193-1649   [73.51669471981023, 15.580992353082049, 9.3382...   
gdb11_s05-57-5967    [73.51669471981023, 22.423817905692996, 24.156...   
gdb11_s07-3769-379   [73.51669471981023, 11.152141192626104, 11.212...   
gdb11_s08-27091-83   [53.3587073998281, 23.5715179759266, 30.188533...   

                        label  
gdb11_s08-1065-136  -3.387656  
gdb11_s04-23-9088   -1.497720  
gdb11_s08-37758-164 -2.712971  
gdb11_s07-1736-599  -1.985845  
gdb11_s07-2195-15   -2.066852  
...                       ...  
gdb11_s08-21374-45  -2.665909  
gdb11_s05-193-1649  -1.562118  
gdb11_s05-57-5967   -1.980084  
gdb11_s07-3769-379  -2.702803  
gdb11_s08-27091-83  -2.065380  

[1000 rows x 4 columns]

### Training and evaluating a model

With features and lables in hand, we're ready to train a model. We use the `GPy` package to train a Gaussian Process Regression (`GPRegression`) model using the Radial Basis Function (`RBF`) kernel.

In [26]:
import GPy
X_train = np.vstack(data_train["feature"])
X_test  = np.vstack(data_test["feature"])
y_train = np.array(data_train["label"])[:,np.newaxis]

kernel = GPy.kern.RBF(
            input_dim=X_train.shape[1])
model = GPy.models.GPRegression(
    X_train, 
    y_train, 
    kernel=kernel)
model.optimize()

model

Using this model, we make predictions for the test and training sets, and evaluate the errors corresponding to those predictions.

In [27]:
data_train["prediction"] = model.predict(X_train)[0][:,0]
data_test["prediction"]  = model.predict(X_test)[0][:,0]

data_train["Unsigned Error (Hartree)"] = np.abs(data_train["label"] - data_train["prediction"])
data_test["Unsigned Error (Hartree)"] = np.abs(data_test["label"] - data_test["prediction"])

Finally, plot the error distributions:

In [28]:
data_train["Dataset"] = "ANI-1 Training Set"
data_test["Dataset"] = "ANI-1 Test Set"
data_joined = data_train.append(data_test)

fig = px.violin(data_joined, y="Unsigned Error (Hartree)", x="Dataset", box=True,
               title="Error Distribution for our ML Model")
fig.show()

### Test on the COMP6 S66x8 benchmark

Again taking advantage of the common data format on QCArchive, we can easily test our model on a different dataset. Here, we use the COMP6 S66x8 benchmark set:

In [29]:
comp6 = client.get_collection("Dataset", "COMP6 S66x8")
print_info(comp6)

Name: COMP6 S66x8

Data Points: 528
Elements: ['C', 'H', 'N', 'O']
Labels: ['energy', 'gradient', 'charges', 'dipole', 'spin density']


Get the molecules and energies from COMP6:

In [30]:
comp6.units = "hartree"
values = comp6.get_values(name="Energy")
molecules= comp6.get_molecules()

An example molecule:

In [31]:
molecules["molecule"][100]

NGLWidget()

----
Repeat the same process as done for ANI-1 to get molecules and energies, generate features and labels, and make predictions.

In [32]:
data = pd.merge(values, molecules, left_index=True, right_index=True)

data["feature"] = [coulomb_matrix(molecule) for molecule in data["molecule"]]
data["label"] = [data.loc[idx, "Energy"] - 
                       free_atom_energy(data.loc[idx, "molecule"])
                       for idx in data.index]
X = np.vstack(data["feature"])
data["prediction"] = model.predict(X)[0][:,0]

data["Unsigned Error (Hartree)"] = np.abs(data["label"] - data["prediction"])
data["Dataset"] = "COMP6 S66x8 Test Set"
data_all = data_joined.append(data, sort=False)
data_all["Method"] = "Our ML Model"

fig = px.violin(data_all, y="Unsigned Error (Hartree)", x="Dataset",
               title="Error Distribution for our ML Model")
fig.show()

# Extras

In [2]:
from IPython.core.display import HTML

def print_info(dataset):
    print(f"Name: {dataset.data.name}")
    print()
    print(f"Data Points: {dataset.data.metadata['data_points']}")
    print(f"Elements: {dataset.data.metadata['elements']}")
    print(f"Labels: {dataset.data.metadata['labels']}")
    
    display(HTML("<u>Description:</u> " + dataset.data.description))
    
    for cite in dataset.data.metadata["citations"]:
        display(HTML(cite['acs_citation']))